In [57]:
import torch
from torch import nn
from torch.utils.data import Dataset
from torchvision.datasets import MNIST

import pandas as pd
import numpy as np
import random

import plotly.express as px
import plotly.subplots as sp
from IPython.display import display
from plotly.offline import init_notebook_mode
init_notebook_mode()

from typing import NoReturn


##  生成1010格式规律的例子


生成真实数据的方法：

In [2]:
generate_real = lambda: torch.FloatTensor([
    random.uniform(0.8, 1),
    random.uniform(0.0, 0.2),
    random.uniform(0.8, 1),
    random.uniform(0.0, 0.2),
])
generate_real.__doc__ = "生成真实数据"


generate_random = lambda size: torch.rand(size)
generate_random.__doc__ = "生成随机噪音"

In [3]:
display(generate_real(), generate_random(4))

tensor([0.8611, 0.1545, 0.8331, 0.0666])

tensor([2.4927e-04, 6.7045e-01, 1.4509e-01, 6.5026e-02])

In [4]:
class Discriminator(nn.Module):
    """判别器
    """

    def __init__(self):
        super().__init__()

        self.model = nn.Sequential(
            nn.Linear(4, 3),
            nn.Sigmoid(),
            nn.Linear(3, 1),
            nn.Sigmoid()
        )

        self.loss_function = nn.MSELoss()

        self.optimiser = torch.optim.SGD(
            self.parameters(),
            lr=0.01
        )

        self.counter = 0
        self.progress = []

    def forward(self, inputs: torch.FloatTensor):
        return self.model(inputs)
    
    def train(
            self,
            inputs: torch.FloatTensor,
            targets: torch.FloatTensor
            ) -> NoReturn:
        outputs = self.forward(inputs)

        loss = self.loss_function(outputs, targets)

        self.counter += 1

        if self.counter % 10 == 0:
            self.progress.append(loss.item())

        if self.counter % 10000 == 0:
            print(f"counter = {self.counter}")

        self.optimiser.zero_grad()
        loss.backward()
        self.optimiser.step()

    def plot_progress(self) -> NoReturn:
        """绘制过程图
        """
        df = pd.DataFrame({
            "step": [i * 10 for i in range(1, len(self.progress) + 1)],
            "loss": self.progress
        })

        fig = px.line(df, x="step", y="loss")
        fig.show()

In [5]:
d = Discriminator()

for i in range(10000):
    d.train(generate_real(), torch.FloatTensor([1.0]))
    d.train(generate_random(4), torch.FloatTensor([0.0]))

counter = 10000
counter = 20000


In [6]:
display(d.forward(generate_real()).item())
display(d.forward(generate_random(4)).item())
d.plot_progress()

0.8212823867797852

0.060312848538160324

In [7]:
class Generator(nn.Module):
    """生成器
    """

    def __init__(self):
        super().__init__()

        self.model = nn.Sequential(
            nn.Linear(1, 3),
            nn.Sigmoid(),
            nn.Linear(3, 4),
            nn.Sigmoid()
        )

        self.optimiser = torch.optim.SGD(
            self.parameters(),
            lr=0.01
        )

        self.counter = 0
        self.progress = []


    def forward(self, inputs: torch.FloatTensor):
        return self.model(inputs)

    def train(
            self,
            d: Discriminator,
            inputs: torch.FloatTensor,
            targets: torch.FloatTensor
        ):
        g_output = self.forward(inputs)
        d_output = d.forward(g_output)
        
        loss = d.loss_function(d_output, targets)

        self.counter += 1
        
        if self.counter % 10 == 0:
            self.progress.append(loss.item())
        
        self.optimiser.zero_grad()
        loss.backward()
        self.optimiser.step()

    def plot_progress(self) -> NoReturn:
        """绘制过程图
        """
        df = pd.DataFrame({
            "step": [i * 10 for i in range(1, len(self.progress) + 1)],
            "loss": self.progress
        })

        fig = px.line(df, x="step", y="loss")
        fig.show()

In [8]:
g = Generator()
g.forward(torch.FloatTensor([0.5]))

tensor([0.6185, 0.5432, 0.4870, 0.5888], grad_fn=<SigmoidBackward0>)

In [9]:
d = Discriminator()
g = Generator()

image_list = []

for i in range(10000):
    if i % 1000 == 0:
        image_list.append(
            g.forward(torch.FloatTensor([0.5])).detach().numpy()
        )
    d.train(generate_real(), torch.FloatTensor([1.0]))

    d.train(
        g.forward(torch.FloatTensor([0.5])).detach(),
        torch.FloatTensor([0.0])
    )

    g.train(
        d,
        torch.FloatTensor([0.5]),
        torch.FloatTensor([1.0])
    )
    

counter = 10000
counter = 20000


In [10]:
d.plot_progress()

In [11]:
g.plot_progress()

In [12]:
g.forward(torch.FloatTensor([0.5]))

tensor([0.8998, 0.0921, 0.8804, 0.0516], grad_fn=<SigmoidBackward0>)

In [13]:
generate_map_df = pd.DataFrame(image_list)
generate_map_df.insert(0, "step", ((generate_map_df.index + 1) * 1000).astype(str))
generate_map_df.columns = generate_map_df.columns.astype(str)

fig = px.density_heatmap(generate_map_df.melt("step"), x="step", y="variable", z="value")
fig.update_traces(dict(colorscale='Tealrose',showscale=True,coloraxis=None),)
fig.show()

## 生成手写数字

In [29]:
mnist_datasets = MNIST('../../general_datasets/', download=True)
px.imshow(mnist_datasets.data[17])

In [30]:
class MNISTDiscriminator(nn.Module):
    """判别器
    """

    def __init__(self):
        super().__init__()

        self.model = nn.Sequential(
            nn.Linear(784, 200),
            nn.Sigmoid(),
            nn.Linear(200, 1),
            nn.Sigmoid()
        )

        self.loss_function = nn.MSELoss()

        self.optimiser = torch.optim.SGD(
            self.parameters(),
            lr=0.01
        )

        self.counter = 0
        self.progress = []

    def forward(self, inputs: torch.FloatTensor):
        return self.model(inputs)
    
    def train(
            self,
            inputs: torch.FloatTensor,
            targets: torch.FloatTensor
            ) -> NoReturn:
        outputs = self.forward(inputs)

        loss = self.loss_function(outputs, targets)

        self.counter += 1

        if self.counter % 10 == 0:
            self.progress.append(loss.item())

        if self.counter % 10000 == 0:
            print(f"counter = {self.counter}")

        self.optimiser.zero_grad()
        loss.backward()
        self.optimiser.step()

    def plot_progress(self) -> NoReturn:
        """绘制过程图
        """
        df = pd.DataFrame({
            "step": [i * 10 for i in range(1, len(self.progress) + 1)],
            "loss": self.progress
        })

        fig = px.line(df, x="step", y="loss")
        fig.show()

训练模型：

In [44]:
mnist_d = MNISTDiscriminator()
for img_data_tensor in mnist_datasets.train_data:
    mnist_d.train(img_data_tensor.reshape((-1,)).float(), torch.FloatTensor([1.0]))
    mnist_d.train(generate_random(784), torch.FloatTensor([0.0]))

mnist_d.plot_progress()

D:\ProgramData\Anaconda3\envs\torch\lib\site-packages\torchvision\datasets\mnist.py:62: UserWarning:

train_data has been renamed data



counter = 10000
counter = 20000
counter = 30000
counter = 40000
counter = 50000
counter = 60000
counter = 70000
counter = 80000
counter = 90000
counter = 100000
counter = 110000
counter = 120000


In [50]:

print("测试手写真实数据：")
for i in range(4):
    img_data_tensor = mnist_datasets\
        .train_data[random.randint(0, 60000)]\
        .reshape((-1,)).float()
    print(mnist_d.forward(img_data_tensor).item())

print("\n测试随机生成器：")
for i in range(4):
    img_data_tensor = generate_random(784)
    print(mnist_d.forward(img_data_tensor).item())

测试手写真实数据：
0.9952248334884644
0.9968834519386292
0.9980629086494446
0.9953710436820984

测试随机生成器：
0.003961907234042883
0.004005823750048876
0.0035882589872926474
0.003811136120930314


In [51]:
class MNISTGenerator(nn.Module):
    """生成器
    """

    def __init__(self):
        super().__init__()

        self.model = nn.Sequential(
            nn.Linear(1, 200),
            nn.Sigmoid(),
            nn.Linear(200, 784),
            nn.Sigmoid()
        )

        self.optimiser = torch.optim.SGD(
            self.parameters(),
            lr=0.01
        )

        self.counter = 0
        self.progress = []


    def forward(self, inputs: torch.FloatTensor):
        return self.model(inputs)

    def train(
            self,
            d: MNISTDiscriminator,
            inputs: torch.FloatTensor,
            targets: torch.FloatTensor
        ):
        g_output = self.forward(inputs)
        d_output = d.forward(g_output)
        
        loss = d.loss_function(d_output, targets)

        self.counter += 1
        
        if self.counter % 10 == 0:
            self.progress.append(loss.item())
        
        self.optimiser.zero_grad()
        loss.backward()
        self.optimiser.step()

    def plot_progress(self) -> NoReturn:
        """绘制过程图
        """
        df = pd.DataFrame({
            "step": [i * 10 for i in range(1, len(self.progress) + 1)],
            "loss": self.progress
        })

        fig = px.line(df, x="step", y="loss")
        fig.show()

In [53]:
mnist_g = MNISTGenerator()
output = mnist_g.forward(generate_random(1))
img = output.detach().numpy().reshape(28, 28)
px.imshow(img)

In [68]:
mnist_d = MNISTDiscriminator()
mnist_g = MNISTGenerator()
for img_data_tensor in mnist_datasets.train_data:
    mnist_d.train(img_data_tensor.reshape((-1,)).float()/255.0, torch.FloatTensor([1.0]))
    mnist_d.train(mnist_g.forward(generate_random(1)).detach(), torch.FloatTensor([0.0]))
    mnist_g.train(mnist_d, generate_random(1), torch.FloatTensor([1.0]))

mnist_d.plot_progress()
mnist_g.plot_progress()

D:\ProgramData\Anaconda3\envs\torch\lib\site-packages\torchvision\datasets\mnist.py:62: UserWarning:

train_data has been renamed data



counter = 10000
counter = 20000
counter = 30000
counter = 40000
counter = 50000
counter = 60000
counter = 70000
counter = 80000
counter = 90000
counter = 100000
counter = 110000
counter = 120000


测试训练的结果：

In [69]:
fig_with_sub = sp.make_subplots(rows=3, cols=3)
for i in range(1, 4):
    for j in range(1, 4):
        fig = px.imshow(
            mnist_g
                .forward(generate_random(1))
                .detach()
                .numpy()
                .reshape(28, 28)
            )
        fig_with_sub.append_trace(
            fig.data[0],
            row=i, col=j
        )
fig_with_sub.show()